# First Neural ODE example

A neural ODE is an ODE where a neural network defines its derivative function. $\dot{u} = NN(u)$

From: https://docs.sciml.ai/DiffEqFlux/stable/examples/neural_ode/

In [1]:
using Lux, DiffEqFlux, DifferentialEquations, ComponentArrays
using Optimization, OptimizationOptimJL, OptimizationOptimisers
using Random, Plots
Plots.default(fmt=:png)

rng = Random.default_rng()

TaskLocalRNG()

True solution

In [2]:
function trueODEfunc(du, u, p, t)
    true_A = [-0.1 2.0; -2.0 -0.1]
    du .= ((u.^3)'true_A)'
end

trueODEfunc (generic function with 1 method)

The data used for training

In [3]:
u0 = Float32[2.0; 0.0]
datasize = 30
tspan = (0.0f0, 1.5f0)
tsteps = range(tspan[begin], tspan[end], length = datasize)
prob_trueode = ODEProblem(trueODEfunc, u0, tspan)
ode_data = Array(solve(prob_trueode, Tsit5(), saveat = tsteps))

2×30 Matrix{Float32}:
 2.0  1.9465    1.74178  1.23837  0.577127  …  1.40688   1.37023   1.29214
 0.0  0.798832  1.46473  1.80877  1.86465      0.451377  0.728699  0.972102

Make a `NeuralODE` problem with a neural network defined by `Lux.jl`.

In [4]:
dudt2 = Lux.Chain(
    x -> x.^3,
    Lux.Dense(2, 50, tanh),
    Lux.Dense(50, 2)
)

p, st = Lux.setup(rng, dudt2)
prob_neuralode = NeuralODE(dudt2, tspan, Tsit5(), saveat = tsteps)

NeuralODE(
    model = Chain(
        layer_1 = WrappedFunction(static(:direct_call), var"#1#2"()),
        layer_2 = Dense(2 => 50, tanh_fast),  # 150 parameters
        layer_3 = Dense(50 => 2),       # 102 parameters
    ),
)         # Total: 252 parameters,
          #        plus 0 states.

Define output, loss, and callback functions.

In [5]:
function predict_neuralode(p)
    Array(prob_neuralode(u0, p, st)[1])
  end

function loss_neuralode(p)
    pred = predict_neuralode(p)
    loss = sum(abs2, ode_data .- pred)
    return loss, pred
end

loss_neuralode (generic function with 1 method)

Do not generate plots by default. Users could change doplot=true to see the figures in the callback fuction.

In [6]:
callback = function (p, l, pred; doplot = false)
    println(l)
    # plot current prediction against data
    if doplot
      plt = scatter(tsteps, ode_data[1,:], label = "data")
      scatter!(plt, tsteps, pred[1,:], label = "prediction")
      plot(plt)
    end
    return false
end

#3 (generic function with 1 method)

Try the callback function on the first iteration.

In [7]:
pinit = ComponentArray(p)
callback(pinit, loss_neuralode(pinit)...; doplot=true)

167.19664


false

Use Optimization.jl to solve the problem.
- `Zygote` for automatic differentiation (AD)
- `loss_neuralode` as the function to be optimized
- Make an `OptimizationProblem`

In [8]:
adtype = Optimization.AutoZygote()
optf = Optimization.OptimizationFunction((x, p) -> loss_neuralode(x), adtype)
optprob = Optimization.OptimizationProblem(optf, pinit)

OptimizationProblem. In-place: true
u0: ComponentVector{Float32}(layer_1 = Float32[], layer_2 = (weight = Float32[0.0662788 -0.32771367; -0.33288264 0.2743391; … ; 0.2683026 -0.21706231; -0.091520146 0.24157134], bias = Float32[0.0; 0.0; … ; 0.0; 0.0;;]), layer_3 = (weight = Float32[0.1532453 -0.116649 … 0.08572113 0.08022476; -0.22498849 -0.16709 … 0.050608143 0.12155518], bias = Float32[0.0; 0.0;;]))

Solve the `OptimizationProblem`.

In [9]:
result_neuralode = Optimization.solve(
    optprob,
    OptimizationOptimisers.ADAM(0.05),
    callback = callback,
    maxiters = 300
)

167.19664


120.31914
108.403946
107.46847
105.21311


100.592
96.75333
95.06156
94.56816


94.15621
93.28329
91.80549
89.79514


87.41507
84.811775
82.02457
78.87979


...

0.19605987
0.26088452
0.18836077


0.13768837
0.18005958
0.20056307


0.16222958
0.13290618
0.15851179


0.13290618


retcode: Default
u: ComponentVector{Float32}(layer_1 = Float32[], layer_2 = (weight = Float32[-0.35651985 0.26343077; -0.10204345 0.11413392; … ; 0.06733824 -0.09214533; -0.25298274 0.015427607], bias = Float32[0.13203104; -0.343761; … ; 0.6513015; -0.46673098;;]), layer_3 = (weight = Float32[-0.6064762 -0.065846846 … 0.13850327 0.42713645; -0.63914734 -0.5337808 … 0.54750055 -0.11272484], bias = Float32[-0.4069189; -0.19255003;;]))

Use another optimization algorithm `Optim.BFGS()` and start from where the `ADAM()` algorithm stopped.

In [10]:
optprob2 = remake(optprob, u0 = result_neuralode.u)

result_neuralode2 = Optimization.solve(
    optprob2,
    Optim.BFGS(initial_stepnorm=0.01),
    callback=callback,
    allow_f_increases = false
)

0.13290618


0.13218533
0.13190852


0.12189339


0.11270843


0.0872243


...

0.006661932


0.00621038


0.006055832


0.006055832


retcode: Success
u: ComponentVector{Float32}(layer_1 = Float32[], layer_2 = (weight = Float32[-0.14090522 0.23728213; -0.106181554 0.12472089; … ; 0.09093609 -0.20473632; -0.2093878 -0.026541697], bias = Float32[0.236187; -0.43054527; … ; 0.72830635; -0.4551798;;]), layer_3 = (weight = Float32[-0.61769265 -0.14475703 … 0.26489532 0.43320486; -0.6611805 -0.7263577 … 0.8093641 -0.2037413], bias = Float32[-0.3718002; 0.20293607;;]))

Plot the solution to see if it matches the provided data.

In [11]:
callback(result_neuralode2.u, loss_neuralode(result_neuralode2.u)...; doplot=true)

0.006055832


false

## Animated solving process
Let's reset the problem and visualize the training process.

In [12]:
rng = Random.default_rng()
u0 = Float32[2.0; 0.0]
datasize = 30
tspan = (0.0f0, 1.5f0)
tsteps = range(tspan[begin], tspan[end], length = datasize)

0.0f0:0.05172414f0:1.5f0

Setup truth values for validation

In [13]:
true_A = Float32[-0.1 2.0; -2.0 -0.1]

function trueODEfunc!(du, u, p, t)
    du .= ((u.^3)'true_A)'
end

trueODEfunc! (generic function with 1 method)

In [14]:
prob_trueode = ODEProblem(trueODEfunc!, u0, tspan)
ode_data = Array(solve(prob_trueode, Tsit5(), saveat = tsteps))

2×30 Matrix{Float32}:
 2.0  1.9465    1.74178  1.23837  0.577126  …  1.40688   1.37023   1.29215
 0.0  0.798832  1.46473  1.80877  1.86465      0.451358  0.728681  0.972087

In [15]:
nodeFunc = Lux.Chain(
    x -> x.^3,
    Lux.Dense(2, 50, tanh),
    Lux.Dense(50, 2)
)

p, st = Lux.setup(rng, nodeFunc)

((layer_1 = NamedTuple(), layer_2 = (weight = Float32[-0.0017697228 0.075023025; -0.03329629 0.13265085; … ; -0.09379381 -0.27755153; -0.17466469 0.3351102], bias = Float32[0.0; 0.0; … ; 0.0; 0.0;;]), layer_3 = (weight = Float32[-0.31938246 -0.012167533 … -0.05699885 0.16791472; 0.1971828 -0.011796937 … 0.20698278 -0.12465175], bias = Float32[0.0; 0.0;;])), (layer_1 = NamedTuple(), layer_2 = NamedTuple(), layer_3 = NamedTuple()))

Parameters in the neural network:

In [16]:
p

(layer_1 = NamedTuple(), layer_2 = (weight = Float32[-0.0017697228 0.075023025; -0.03329629 0.13265085; … ; -0.09379381 -0.27755153; -0.17466469 0.3351102], bias = Float32[0.0; 0.0; … ; 0.0; 0.0;;]), layer_3 = (weight = Float32[-0.31938246 -0.012167533 … -0.05699885 0.16791472; 0.1971828 -0.011796937 … 0.20698278 -0.12465175], bias = Float32[0.0; 0.0;;]))

Use `NeuroODE()` to construct the problem

In [17]:
prob_node = NeuralODE(nodeFunc, tspan, Tsit5(), saveat = tsteps)

NeuralODE(
    model = Chain(
        layer_1 = WrappedFunction(static(:direct_call), var"#8#9"()),
        layer_2 = Dense(2 => 50, tanh_fast),  # 150 parameters
        layer_3 = Dense(50 => 2),       # 102 parameters
    ),
)         # Total: 252 parameters,
          #        plus 0 states.

Predicted values.

In [18]:
function predict_neuralode(p)
    Array(prob_node(u0, p, st)[1])
end

predict_neuralode (generic function with 1 method)

The loss function.

In [19]:
function loss_neuralode(p)
    pred = predict_neuralode(p)
    loss = sum(abs2, ode_data .- pred)
    return loss, pred
end

loss_neuralode (generic function with 1 method)

Callback function to observe training process

In [20]:
anim = Animation()
callback = function (p, l, pred; doplot = true)
    if doplot
        plt = scatter(tsteps, ode_data[1,:], label = "data")
        scatter!(plt, tsteps, pred[1,:], label = "prediction")
        frame(anim)
    end
    return false
end

#10 (generic function with 1 method)

In [21]:
adtype = Optimization.AutoZygote()
optf = Optimization.OptimizationFunction((x, p) -> loss_neuralode(x), adtype)
optprob = Optimization.OptimizationProblem(optf, ComponentArray(p))

OptimizationProblem. In-place: true
u0: ComponentVector{Float32}(layer_1 = Float32[], layer_2 = (weight = Float32[-0.0017697228 0.075023025; -0.03329629 0.13265085; … ; -0.09379381 -0.27755153; -0.17466469 0.3351102], bias = Float32[0.0; 0.0; … ; 0.0; 0.0;;]), layer_3 = (weight = Float32[-0.31938246 -0.012167533 … -0.05699885 0.16791472; 0.1971828 -0.011796937 … 0.20698278 -0.12465175], bias = Float32[0.0; 0.0;;]))

Solve the problem using the ADAM optimizer

In [22]:
result_neuralode = Optimization.solve(
    optprob,
    OptimizationOptimisers.ADAM(0.05),
    callback = callback,
    maxiters = 300
)

retcode: Default
u: ComponentVector{Float32}(layer_1 = Float32[], layer_2 = (weight = Float32[0.60198385 0.4751431; 0.91905576 -0.44151247; … ; 0.24059728 -0.6173106; -1.0068108 0.010679541], bias = Float32[-0.053559765; 0.11342683; … ; -0.1158054; -0.27371103;;]), layer_3 = (weight = Float32[0.24937321 0.79998964 … 0.4535362 -0.03008947; 0.7118856 0.7973566 … 0.26106736 -0.58793104], bias = Float32[-0.59332967; -0.11879284;;]))

And then solve the problem using the LBFGS optimizer

In [23]:
optprob2 = remake(optprob, u0 = result_neuralode.u)

result_neuralode2 = Optimization.solve(
    optprob2,
    Optim.LBFGS(),
    callback = callback,
    allow_f_increases = false
)

retcode: Success
u: ComponentVector{Float32}(layer_1 = Float32[], layer_2 = (weight = Float32[0.55711615 0.32786527; 0.8842164 -0.41041452; … ; 0.1308622 -0.6185396; -1.0092094 -0.02800535], bias = Float32[-0.056156855; 0.09885336; … ; -0.11396651; -0.21055597;;]), layer_3 = (weight = Float32[0.2577177 0.8306918 … 0.5498645 -0.042159688; 0.6751993 0.73580015 … 0.3830905 -0.5592567], bias = Float32[-0.49717152; 0.147061;;]))

Visualize fitting process

In [24]:
mp4(anim, fps=15)

[ Info: Saved animation to /home/runner/work/jl-ude/jl-ude/docs/tmp.mp4


Plots.AnimatedGif("/home/runner/work/jl-ude/jl-ude/docs/tmp.mp4")